In [2]:
!nvidia-smi

Wed Aug 14 09:47:40 2024       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 560.81                 Driver Version: 560.81         CUDA Version: 12.6     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                  Driver-Model | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA GeForce RTX 3050 ...  WDDM  |   00000000:01:00.0 Off |                  N/A |
| N/A   54C    P8              3W /   90W |       0MiB /   6144MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [3]:
pip install chart-studio

Note: you may need to restart the kernel to use updated packages.


In [1]:
import pandas as pd
import tensorflow as tf
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split

import unicodedata
import re
import numpy as np
import time
import string

import chart_studio.plotly
import chart_studio.plotly as py
from plotly.offline import init_notebook_mode, iplot
import plotly.graph_objs as go

import os
for dirname, _, filenames in os.walk('./'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

./Neural_Machine_Translation.ipynb
./por.txt
./.venv\pyvenv.cfg
./.venv\etc\jupyter\nbconfig\notebook.d\jupyterlab-plotly.json
./.venv\Lib\site-packages\decorator.py
./.venv\Lib\site-packages\distutils-precedence.pth
./.venv\Lib\site-packages\ipykernel_launcher.py
./.venv\Lib\site-packages\jupyter.py
./.venv\Lib\site-packages\nest_asyncio.py
./.venv\Lib\site-packages\numpy-1.26.4-cp310-cp310-win_amd64.whl
./.venv\Lib\site-packages\pylab.py
./.venv\Lib\site-packages\pythoncom.py
./.venv\Lib\site-packages\PyWin32.chm
./.venv\Lib\site-packages\pywin32.pth
./.venv\Lib\site-packages\pywin32.version.txt
./.venv\Lib\site-packages\retrying.py
./.venv\Lib\site-packages\scipy-1.14.0-cp310-cp310-win_amd64.whl
./.venv\Lib\site-packages\six.py
./.venv\Lib\site-packages\threadpoolctl.py
./.venv\Lib\site-packages\typing_extensions.py
./.venv\Lib\site-packages\absl\app.py
./.venv\Lib\site-packages\absl\app.pyi
./.venv\Lib\site-packages\absl\command_name.py
./.venv\Lib\site-packages\absl\__init__.py
./

In [2]:
file_path='por.txt'

In [3]:
lines=open(file_path,'r',encoding='utf-8').read().strip().split('\n')

In [4]:
lines[5000:5010]

['Will it rain?\tSerá que chove?\tCC-BY 2.0 (France) Attribution: tatoeba.org #8918600 (CK) & #8930552 (JGEN)',
 'Wish me luck.\tDeseje-me sorte.\tCC-BY 2.0 (France) Attribution: tatoeba.org #2254917 (CK) & #872788 (alexmarcelo)',
 "Won't you go?\tVocê não vai?\tCC-BY 2.0 (France) Attribution: tatoeba.org #241051 (CK) & #6212788 (bill)",
 'Write in ink.\tEscreva à tinta.\tCC-BY 2.0 (France) Attribution: tatoeba.org #3258764 (CM) & #7351595 (alexmarcelo)',
 'Write in ink.\tEscreva a tinta.\tCC-BY 2.0 (France) Attribution: tatoeba.org #3258764 (CM) & #7351606 (alexmarcelo)',
 'Write to Tom.\tEscreva para o Tom.\tCC-BY 2.0 (France) Attribution: tatoeba.org #2240357 (CK) & #5985551 (Ricardo14)',
 'Years passed.\tPassaram os anos.\tCC-BY 2.0 (France) Attribution: tatoeba.org #282197 (CK) & #977841 (alexmarcelo)',
 'Years passed.\tAnos se passaram.\tCC-BY 2.0 (France) Attribution: tatoeba.org #282197 (CK) & #2324530 (Matheus)',
 'You amuse me.\tVocê me diverte.\tCC-BY 2.0 (France) Attributio

In [5]:
print("Total number of Lines:",len(lines))

Total number of Lines: 168903


In [6]:
exclude=set(string.punctuation)
remove_digits=str.maketrans('','',string.digits)

In [7]:
def pre_process_eng(sentence):
  sentence=sentence.lower()
  sentence=re.sub("'",'',sentence)
  sentence=''.join(ch for ch in sentence if ch not in exclude)
  sentence=sentence.translate(remove_digits)
  sentence=sentence.strip()
  sentence = re.sub(" +", " ", sentence)
  sentence = '<start> ' + sentence + ' <end>'
  return sentence

In [8]:
def pre_process_port(sentence):
  sentence=re.sub("'",'',sentence)
  sentence=''.join(ch for ch in sentence if ch not in exclude)
  sentence=sentence.strip()
  sentence = re.sub(" +", " ", sentence)
  sentence = '<start> ' + sentence + ' <end>'
  return sentence

In [9]:
sentence_pairs=[]
for line in lines:
  sentence_pair=[]
  eng=line.rstrip().split('\t')[0]
  port=line.rstrip().split('\t')[1]
  eng=pre_process_eng(eng)
  port=pre_process_port(port)
  sentence_pair.append(eng)
  sentence_pair.append(port)
  sentence_pairs.append(sentence_pair)
sentence_pairs

[['<start> go <end>', '<start> Vai <end>'],
 ['<start> go <end>', '<start> Vá <end>'],
 ['<start> hi <end>', '<start> Oi <end>'],
 ['<start> run <end>', '<start> Corre <end>'],
 ['<start> run <end>', '<start> Corra <end>'],
 ['<start> run <end>', '<start> Corram <end>'],
 ['<start> run <end>', '<start> Corre <end>'],
 ['<start> run <end>', '<start> Corra <end>'],
 ['<start> run <end>', '<start> Corram <end>'],
 ['<start> who <end>', '<start> Quem <end>'],
 ['<start> who <end>', '<start> Que <end>'],
 ['<start> wow <end>', '<start> Uau <end>'],
 ['<start> wow <end>', '<start> Nossa <end>'],
 ['<start> wow <end>', '<start> Wow <end>'],
 ['<start> fire <end>', '<start> Fogo <end>'],
 ['<start> fire <end>', '<start> Incêndio <end>'],
 ['<start> fire <end>', '<start> Chama <end>'],
 ['<start> help <end>', '<start> Ajuda <end>'],
 ['<start> help <end>', '<start> Socorro <end>'],
 ['<start> jump <end>', '<start> Pule <end>'],
 ['<start> jump <end>', '<start> Pula <end>'],
 ['<start> jump <end

In [10]:
class LanguageIndex():
    def __init__(self, lang):
        self.lang = lang
        self.word2idx = {}
        self.idx2word = {}
        self.vocab = set()
        self.create_index()
    def create_index(self):
        for phrase in self.lang:
            self.vocab.update(phrase.split(' '))
        self.vocab = sorted(self.vocab)
        self.word2idx['<pad>'] = 0
        for index, word in enumerate(self.vocab):
            self.word2idx[word] = index + 1
        for word, index in self.word2idx.items():
            self.idx2word[index] = word

In [11]:
def max_length(tensor):
    return max(len(t) for t in tensor)

In [12]:
def load_dataset(pairs, num_examples):
    inp_lang = LanguageIndex(en for en, ma in pairs)
    targ_lang = LanguageIndex(ma for en, ma in pairs)
    input_tensor = [[inp_lang.word2idx[s] for s in en.split(' ')] for en, ma in pairs]
    target_tensor = [[targ_lang.word2idx[s] for s in ma.split(' ')] for en, ma in pairs]
    max_length_inp, max_length_tar = max_length(input_tensor), max_length(target_tensor)
    input_tensor = tf.keras.preprocessing.sequence.pad_sequences(input_tensor,
                                                                 maxlen=max_length_inp,
                                                                 padding='post')
    target_tensor = tf.keras.preprocessing.sequence.pad_sequences(target_tensor,
                                                                  maxlen=max_length_tar,
                                                                  padding='post')
    return input_tensor, target_tensor, inp_lang, targ_lang, max_length_inp, max_length_tar

In [13]:
input_tensor,target_tensor,inp_lang,targ_lang,max_length_inp,max_length_targ=load_dataset(sentence_pairs,len(lines))

In [14]:
input_tensor_train, input_tensor_val, target_tensor_train, target_tensor_val = train_test_split(input_tensor, target_tensor, test_size=0.1, random_state = 101)
len(input_tensor_train), len(target_tensor_train), len(input_tensor_val), len(target_tensor_val)

(152012, 152012, 16891, 16891)

In [15]:
BUFFER_SIZE = len(input_tensor_train)
BATCH_SIZE = 64
N_BATCH = BUFFER_SIZE//BATCH_SIZE
embedding_dim = 256
units = 1024
vocab_inp_size = len(inp_lang.word2idx)
vocab_tar_size = len(targ_lang.word2idx)
print(vocab_inp_size,vocab_tar_size)
dataset = tf.data.Dataset.from_tensor_slices((input_tensor_train, target_tensor_train)).shuffle(BUFFER_SIZE)
dataset = dataset.batch(BATCH_SIZE, drop_remainder=True)

12653 25091


In [16]:
def gru(units):
  return tf.keras.layers.GRU(units,
                           return_sequences=True,
                           return_state=True,
                           recurrent_initializer='glorot_uniform')

In [17]:
class Encoder(tf.keras.Model):
   def __init__(self, vocab_size, embedding_dim, enc_units, batch_sz):
        super(Encoder, self).__init__()
        self.batch_sz = batch_sz
        self.enc_units = enc_units
        self.embedding = tf.keras.layers.Embedding(vocab_size, embedding_dim)
        self.gru = gru(self.enc_units)

   def call(self, x, hidden):
        x = self.embedding(x)
        output, state = self.gru(x, initial_state = hidden)
        return output, state

   def initialize_hidden_state(self):
        return tf.zeros((self.batch_sz, self.enc_units))

In [18]:
class Decoder(tf.keras.Model):
    def __init__(self, vocab_size, embedding_dim, dec_units, batch_sz):
        super(Decoder, self).__init__()
        self.batch_sz = batch_sz
        self.dec_units = dec_units
        self.embedding = tf.keras.layers.Embedding(vocab_size, embedding_dim)
        self.gru = gru(self.dec_units)
        self.fc = tf.keras.layers.Dense(vocab_size)
        # used for attention
        self.W1 = tf.keras.layers.Dense(self.dec_units)
        self.W2 = tf.keras.layers.Dense(self.dec_units)
        self.V = tf.keras.layers.Dense(1)

    def call(self, x, hidden, enc_output):
        hidden_with_time_axis = tf.expand_dims(hidden, 1)
        # score shape == (batch_size, max_length, 1)
        # we get 1 at the last axis because we are applying tanh(FC(EO) + FC(H)) to self.V
        score = self.V(tf.nn.tanh(self.W1(enc_output) + self.W2(hidden_with_time_axis)))
        # attention_weights shape == (batch_size, max_length, 1)
        attention_weights = tf.nn.softmax(score, axis=1)
        # context_vector shape after sum == (batch_size, hidden_size)
        context_vector = attention_weights * enc_output
        context_vector = tf.reduce_sum(context_vector, axis=1)
        # x shape after passing through embedding == (batch_size, 1, embedding_dim)
        x = self.embedding(x)
        # x shape after concatenation == (batch_size, 1, embedding_dim + hidden_size)
        x = tf.concat([tf.expand_dims(context_vector, 1), x], axis=-1)
        # passing the concatenated vector to the GRU
        output, state = self.gru(x)
        # output shape == (batch_size * 1, hidden_size)
        output = tf.reshape(output, (-1, output.shape[2]))
        # output shape == (batch_size * 1, vocab)
        x = self.fc(output)
        return x, state, attention_weights

    def initialize_hidden_state(self):
        return tf.zeros((self.batch_sz, self.dec_units))

In [19]:
encoder = Encoder(vocab_inp_size, embedding_dim, units, BATCH_SIZE)
decoder = Decoder(vocab_tar_size, embedding_dim, units, BATCH_SIZE)

In [20]:
optimizer=tf.keras.optimizers.Adam()

In [21]:
def loss_function(real,pred):
  mask = 1 - np.equal(real, 0)
  loss_ = tf.nn.sparse_softmax_cross_entropy_with_logits(labels=real, logits=pred) * mask
  return tf.reduce_mean(loss_)

In [22]:
checkpoint_dir = './training_checkpoints'
checkpoint_prefix = os.path.join(checkpoint_dir, "ckpt")
checkpoint = tf.train.Checkpoint(optimizer=optimizer,
                                 encoder=encoder,
                                 decoder=decoder)

In [26]:
EPOCHS=10
for epoch in range(EPOCHS):
    start = time.time()
    hidden = encoder.initialize_hidden_state()
    total_loss = 0
    for (batch, (inp, targ)) in enumerate(dataset):
        loss = 0
        with tf.GradientTape() as tape:
            enc_output, enc_hidden = encoder(inp, hidden)
            dec_hidden = enc_hidden
            dec_input = tf.expand_dims([targ_lang.word2idx['<start>']] * BATCH_SIZE, 1)
            # Teacher forcing - feeding the target as the next input
            for t in range(1, targ.shape[1]):
                predictions, dec_hidden, _ = decoder(dec_input, dec_hidden, enc_output)
                loss += loss_function(targ[:, t], predictions)
                dec_input = tf.expand_dims(targ[:, t], 1)

        batch_loss = (loss / int(targ.shape[1]))
        total_loss += batch_loss
        variables = encoder.variables + decoder.variables
        gradients = tape.gradient(loss, variables)
        optimizer.apply_gradients(zip(gradients, variables))
        if batch % 100 == 0:
            print('Epoch {} Batch {} Loss {:.4f}'.format(epoch + 1,
                                                         batch,
                                                         batch_loss.numpy()))
    # saving (checkpoint) the model every epoch
    checkpoint.save(file_prefix = checkpoint_prefix)
    print('Epoch {} Loss {:.4f}'.format(epoch + 1,total_loss / N_BATCH))
    print('Time taken for 1 epoch {} sec\n'.format(time.time() - start))

c:\Users\Sayantan Kanjilal\Documents\neural_translation\.venv\lib\site-packages\keras\src\optimizers\base_optimizer.py:664: UserWarning:

Gradients do not exist for variables ['seed_generator_state', 'seed_generator_state'] when minimizing the loss. If using `model.compile()`, did you forget to provide a `loss` argument?



Epoch 1 Batch 0 Loss 2.0035
Epoch 1 Batch 100 Loss 1.1675
Epoch 1 Batch 200 Loss 1.0784
Epoch 1 Batch 300 Loss 1.1135
Epoch 1 Batch 400 Loss 0.9123
Epoch 1 Batch 500 Loss 1.0081
Epoch 1 Batch 600 Loss 0.8867
Epoch 1 Batch 700 Loss 0.9120
Epoch 1 Batch 800 Loss 0.8137
Epoch 1 Batch 900 Loss 0.7974
Epoch 1 Batch 1000 Loss 0.8221
Epoch 1 Batch 1100 Loss 0.6891
Epoch 1 Batch 1200 Loss 0.7558
Epoch 1 Batch 1300 Loss 0.8283
Epoch 1 Batch 1400 Loss 0.6805
Epoch 1 Batch 1500 Loss 0.5677
Epoch 1 Batch 1600 Loss 0.5978
Epoch 1 Batch 1700 Loss 0.6102
Epoch 1 Batch 1800 Loss 0.5224
Epoch 1 Batch 1900 Loss 0.5075
Epoch 1 Batch 2000 Loss 0.4993
Epoch 1 Batch 2100 Loss 0.4543
Epoch 1 Batch 2200 Loss 0.4548
Epoch 1 Batch 2300 Loss 0.4648
Epoch 1 Loss 0.7709
Time taken for 1 epoch 16850.670236349106 sec

Epoch 2 Batch 0 Loss 0.4992
Epoch 2 Batch 100 Loss 0.3274
Epoch 2 Batch 200 Loss 0.3793
Epoch 2 Batch 300 Loss 0.4542
Epoch 2 Batch 400 Loss 0.3866
Epoch 2 Batch 500 Loss 0.3726
Epoch 2 Batch 600 Loss 

In [23]:
checkpoint.restore(tf.train.latest_checkpoint(checkpoint_dir))

In [24]:
def evaluate(inputs, encoder, decoder, inp_lang, targ_lang, max_length_inp, max_length_targ):
    attention_plot = np.zeros((max_length_targ, max_length_inp))
    sentence = ''
    for i in inputs[0]:
        if i == 0:
            break
        sentence = sentence + inp_lang.idx2word[i] + ' '
    sentence = sentence[:-1]
    inputs = tf.convert_to_tensor(inputs)
    result = ''
    hidden = [tf.zeros((1, units))]
    enc_out, enc_hidden = encoder(inputs, hidden)
    dec_hidden = enc_hidden
    dec_input = tf.expand_dims([targ_lang.word2idx['<start>']], 0)
    for t in range(max_length_targ):
        predictions, dec_hidden, attention_weights = decoder(dec_input, dec_hidden, enc_out)
        attention_weights = tf.reshape(attention_weights, (-1, ))
        attention_plot[t] = attention_weights.numpy()
        predicted_id = tf.argmax(predictions[0]).numpy()
        result += targ_lang.idx2word[predicted_id] + ' '
        if targ_lang.idx2word[predicted_id] == '<end>':
            return result, sentence, attention_plot
        # the predicted ID is fed back into the model
        dec_input = tf.expand_dims([predicted_id], 0)
    return result, sentence, attention_plot

In [25]:
def predict_random_val_sentence():
    actual_sent = ''
    k = np.random.randint(len(input_tensor_val))
    random_input = input_tensor_val[k]
    random_output = target_tensor_val[k]
    random_input = np.expand_dims(random_input,0)
    result, sentence, attention_plot = evaluate(random_input, encoder, decoder, inp_lang, targ_lang, max_length_inp, max_length_targ)
    print('Input: {}'.format(sentence[8:-6]))
    print('Predicted translation: {}'.format(result[:-6]))
    for i in random_output:
        if i == 0:
            break
        actual_sent = actual_sent + targ_lang.idx2word[i] + ' '
    actual_sent = actual_sent[8:-7]
    print('Actual translation: {}'.format(actual_sent))
    attention_plot = attention_plot[:len(result.split(' '))-2, 1:len(sentence.split(' '))-1]
    sentence, result = sentence.split(' '), result.split(' ')
    sentence = sentence[1:-1]
    result = result[:-2]
    trace = go.Heatmap(z = attention_plot, x = sentence, y = result, colorscale='greens')
    data=[trace]
    iplot(data)

In [26]:
predict_random_val_sentence()

c:\Users\Sayantan Kanjilal\Documents\neural_translation\.venv\lib\site-packages\keras\src\layers\layer.py:1331: UserWarning:

Layer 'encoder' looks like it has unbuilt state, but Keras is not able to trace the layer `call()` in order to build it automatically. Possible causes:
1. The `call()` method of your layer may be crashing. Try to `__call__()` the layer eagerly on some test input first to see if it works. E.g. `x = np.random.random((3, 4)); y = layer(x)`
2. If the `call()` method is correct, then you may need to implement the `def build(self, input_shape)` method on your layer. It should create all variables used by the layer (e.g. by calling `layer.build()` on all its children layers).
Exception encountered: '''tensorflow.python.framework.ops.EagerTensor' object has no attribute '_serialize_to_tensors'''

c:\Users\Sayantan Kanjilal\Documents\neural_translation\.venv\lib\site-packages\keras\src\layers\layer.py:372: UserWarning:

`build()` was called on layer 'encoder', however th

Input: tom got out of the bathtub
Predicted translation: omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omele
Actual translation: Tom saiu da banheira


In [27]:
predict_random_val_sentence()

Input: she told me about what she saw in australia
Predicted translation: omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omele
Actual translation: Ela me contou o que viu na Austrália


In [28]:
predict_random_val_sentence()

Input: what do you want to do tomorrow
Predicted translation: omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omele
Actual translation: O que quer fazer amanhã


In [29]:
predict_random_val_sentence()

Input: theres room for everyone
Predicted translation: grande de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omele
Actual translation: Tem lugar pra todo mundo


In [30]:
predict_random_val_sentence()

Input: they dont make you happy
Predicted translation: grande de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omelete de seu omele
Actual translation: Eles não fazem você feliz
